In [130]:
import time
from bs4 import BeautifulSoup
import sys, io
from selenium import webdriver
from selenium.common.exceptions import StaleElementReferenceException
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.common.proxy import *
from joblib import load, dump
import pandas as pd
from decimal import Decimal

In [131]:
driver = webdriver.Chrome('./chromedriver')
wait = WebDriverWait( driver, 10 )
URL = "https://www.airbnb.com/s/New-York--NY/homes?place_id=ChIJOwg_06VPwokRYv534QaPC8g&refinement_paths%5B%5D=%2Fhomes&search_type=search_query&tab_id=home_tab&query=New%20York%2C%20NY&checkin=2020-08-01&checkout=2020-08-02&adults=1&source=structured_search_input_header"

In [132]:
# Scraping is very finicky. If a tag is missing, the whole thing could fail. 
# If the website format changes, then the scraping will UNDOUBTEDLY fail. 
# Please check to make sure these CSS classes are still relevant 
def scrape_airbnb_data(driver):
    page = driver.page_source # Grab Airbnb Listing page source 
    soup_expansion = BeautifulSoup(page, 'html.parser') # Parse the page with beautiful soup 
    
    # Grab the neighborhood of the listing 
    address = soup_expansion.find('a', class_='_5twioja') 
    print('address: ', address)
    airbnb_address = address.get_text() if address != None else 'Not Found'
    
    # Grab the name of the listing
    airbnb_name_tag = soup_expansion.find('h1', class_='_18hrqvin') if soup_expansion.find('h1', class_='_14i3z6h') == None else soup_expansion.find('h1', class_='_14i3z6h') 
    print('airbnb_name_tag: ', airbnb_name_tag) 
    airbnb_name = airbnb_name_tag.get_text() if airbnb_name_tag != None else 'Not Found'
    
    # Grab the price of the listing
    price_tag = soup_expansion.find('span', class_='_pgfqnw')
    print('price_tag: ', price_tag)
    price = 0
    if price_tag != None:
        price_string = price_tag.get_text()
        price_string = price_string.replace('$','')
        price_string = price_string.replace(',','')
        price = int(price_string)
        
    # Grab the number of reviews AND Primary Rating for this particular listing
    # (On the webpage these are stored right next to eachother so why not)
    num_reviews_tag = soup_expansion.find('span', class_='_goo6eo')
    print('num_reviews_tag: ', num_reviews_tag)
    num_reviews = 0
    primary_rating = 0
    if num_reviews_tag != None:
        try:
            num_reviews_tag = num_reviews_tag.find('div')
            num_reviews_string = num_reviews_tag.get_text()
            num_reviews = int(num_reviews_string.split(' ')[1].replace('(', ''))
            primary_rating = Decimal(num_reviews_string.split(' ')[0].replace(',', ''))
        except:
            print('unable to get num_reviews: ', num_reviews_string)

    # Grab the ratings of the other metrics 
    secondary_ratings = soup_expansion.find_all('span', class_='_4oybiu')
    print('secondary_ratings: ', secondary_ratings)
    metrics = [None, None, None, None, None, None]
    for i, rating in enumerate(secondary_ratings):
        metrics[i] = Decimal(rating.get_text())
    
    # Get the amenities for this listing and store them in a list 
    amenities_tag = soup_expansion.find_all('div', class_='_1nlbjeu')
    print('amenities_tag: ', amenities_tag)
    amenities = []
    for amenity in amenities_tag:
        amenities.append(amenity.get_text())
    
    # Return our observation for the dataframe
    return {'Airbnb_Name': airbnb_name, 
            'Price': price, 
            'Primary_Rating': primary_rating, 
            'Location_Rating': metrics[0], 
            'Cleanliness_Rating': metrics[1],  
            'Value_Rating': metrics[2], 
            'Communication_Rating': metrics[3],
            'Accuracy_Rating': metrics[4],
            'Checkin_Rating': metrics[5],
            'Num_Reviews': num_reviews,
            'Neighborhood': airbnb_address,
            'Amenities': amenities}

In [133]:
driver.get(URL) 
time.sleep(2)
df = pd.DataFrame(columns=['Airbnb_Name', 
                           'Price', 
                           'Primary_Rating', 
                           'Location_Rating', 
                           'Cleanliness_Rating',  
                           'Value_Rating',
                           'Communication_Rating',
                           'Accuracy_Rating',
                           'Checkin_Rating',
                           'Num_Reviews',
                           'Neighborhood',
                           'Amenities'])
next_button = True

home_tab = driver.window_handles[0]

# While we still have a next page button, keep scraping
# All the time.sleep calls help the page load. 
while(next_button != None):
    time.sleep(2)
    # Grab all the page listings
    airbnb_listings = driver.find_elements_by_class_name('_i24ijs')
    time.sleep(2)
    
    # For each listing on the page 
    # we start from 1 because the first element for the class '_i24ijs' is not a listing 
    for i in range(1, len(airbnb_listings)): 
        airbnb_listing = airbnb_listings[i]
        
        # Go to that particular listing's page 
        driver.execute_script("arguments[0].click();", airbnb_listing);
        time.sleep(5)
        try:
            tabs = driver.window_handles # Get the home tab and the tab we opened the listing on 
            tabs.remove(home_tab)
            opened_tab = tabs[-1]
            driver.switch_to.window(opened_tab) # Switch to the opened tab 
            time.sleep(2)
            print('Title: ', driver.title) # Grab the data from the page the driver is on  
            df = df.append(scrape_airbnb_data(driver), ignore_index=True)
            time.sleep(2)
            driver.close()
            driver.switch_to.window(home_tab) # Close the current listing and switch back the home tab 
        except StaleElementReferenceException:
            driver.refresh()
            break
            print('Error, skipping airbnb listing')
    time.sleep(2)
    # How to select multiple classes: http://makeseleniumeasy.com/2017/09/26/how-to-locate-web-element-which-has-multiple-class-names/
    
    # We finished scraping all the current listings, moving on to the next page
    next_button = driver.find_element_by_css_selector("a._1li8g8e")
    driver.execute_script("arguments[0].scrollIntoView()", next_button);
    driver.execute_script("arguments[0].click();", next_button);
    airbnb_listings = []
    # next_button.click() # avoid using this so we don't get stale element reference!        

dump(df, 'airbnb_dataframe.pkl', compress=True)
df.to_csv('airbnb_hotels.csv')

Title:  City King - Boutique hotels for Rent in New York, New York, United States
address:  <a class="_5twioja" href="https://airbnb.com/s/New%20York/homes" rel="noopener noreferrer" target="_blank">New York, United States</a>
airbnb_name_tag:  <h1 class="_14i3z6h" tabindex="-1">City King</h1>
price_tag:  <span aria-hidden="true" class="_pgfqnw">$79</span>
num_reviews_tag:  <span class="_goo6eo"><span class="_krjbj">4.93 out of 5 stars from 14 reviews</span><div dir="ltr">4.93 (14 reviews)</div></span>
secondary_ratings:  [<span aria-hidden="true" class="_4oybiu">4.9</span>, <span aria-hidden="true" class="_4oybiu">5.0</span>, <span aria-hidden="true" class="_4oybiu">4.4</span>, <span aria-hidden="true" class="_4oybiu">4.7</span>, <span aria-hidden="true" class="_4oybiu">4.1</span>, <span aria-hidden="true" class="_4oybiu">4.7</span>]
amenities_tag:  [<div class="_1nlbjeu"><div>Wifi</div><div class="_yp1t7a"><svg aria-hidden="true" role="presentation" style="display: block; height: 24p

num_reviews_tag:  <span class="_goo6eo"><span class="_krjbj">4.66 out of 5 stars from 187 reviews</span><div dir="ltr">4.66 (187 reviews)</div></span>
secondary_ratings:  [<span aria-hidden="true" class="_4oybiu">4.5</span>, <span aria-hidden="true" class="_4oybiu">4.8</span>, <span aria-hidden="true" class="_4oybiu">4.9</span>, <span aria-hidden="true" class="_4oybiu">4.4</span>, <span aria-hidden="true" class="_4oybiu">4.9</span>, <span aria-hidden="true" class="_4oybiu">4.8</span>]
amenities_tag:  [<div class="_1nlbjeu"><div>Kitchen</div><div class="_yp1t7a"><svg aria-hidden="true" role="presentation" style="display: block; height: 24px; width: 24px; fill: currentcolor;" viewbox="0 0 32 32" xmlns="http://www.w3.org/2000/svg"><path d="M26 1a5 5 0 0 1 5 5c0 6.389-1.592 13.187-4 14.693V31h-2V20.694c-2.364-1.478-3.942-8.062-3.998-14.349L21 6l.005-.217A5 5 0 0 1 26 1zm-9 0v18.118c2.317.557 4 3.01 4 5.882 0 3.27-2.183 6-5 6s-5-2.73-5-6c0-2.872 1.683-5.326 4-5.882V1zM2 1h1c4.47 0 6.934 6.3

Title:  Cozy, comfort close to LaGuardia Airport - Houses for Rent in East Elmhurst, New York, United States
address:  <a class="_5twioja" href="https://airbnb.com/s/East%20Elmhurst/homes" rel="noopener noreferrer" target="_blank">East Elmhurst, New York, United States</a>
airbnb_name_tag:  <h1 class="_14i3z6h" tabindex="-1">Cozy, comfort close to LaGuardia Airport</h1>
price_tag:  <span aria-hidden="true" class="_pgfqnw">$30</span>
num_reviews_tag:  <span class="_goo6eo"><span class="_krjbj">4.94 out of 5 stars from 17 reviews</span><div dir="ltr">4.94 (17 reviews)</div></span>
secondary_ratings:  [<span aria-hidden="true" class="_4oybiu">4.9</span>, <span aria-hidden="true" class="_4oybiu">4.8</span>, <span aria-hidden="true" class="_4oybiu">4.8</span>, <span aria-hidden="true" class="_4oybiu">4.9</span>, <span aria-hidden="true" class="_4oybiu">5.0</span>, <span aria-hidden="true" class="_4oybiu">4.9</span>]
amenities_tag:  [<div class="_1nlbjeu"><div>Free parking on premises</div><

secondary_ratings:  [<span aria-hidden="true" class="_4oybiu">4.9</span>, <span aria-hidden="true" class="_4oybiu">4.9</span>, <span aria-hidden="true" class="_4oybiu">4.9</span>, <span aria-hidden="true" class="_4oybiu">4.5</span>, <span aria-hidden="true" class="_4oybiu">4.9</span>, <span aria-hidden="true" class="_4oybiu">4.9</span>]
amenities_tag:  [<div class="_1nlbjeu"><div>Kitchen</div><div class="_yp1t7a"><svg aria-hidden="true" role="presentation" style="display: block; height: 24px; width: 24px; fill: currentcolor;" viewbox="0 0 32 32" xmlns="http://www.w3.org/2000/svg"><path d="M26 1a5 5 0 0 1 5 5c0 6.389-1.592 13.187-4 14.693V31h-2V20.694c-2.364-1.478-3.942-8.062-3.998-14.349L21 6l.005-.217A5 5 0 0 1 26 1zm-9 0v18.118c2.317.557 4 3.01 4 5.882 0 3.27-2.183 6-5 6s-5-2.73-5-6c0-2.872 1.683-5.326 4-5.882V1zM2 1h1c4.47 0 6.934 6.365 6.999 18.505L10 21H3.999L4 31H2zm14 20c-1.602 0-3 1.748-3 4s1.398 4 3 4 3-1.748 3-4-1.398-4-3-4zM4 3.239V19h3.995l-.017-.964-.027-.949C7.673 9.157 6

Title:  Heart of Hell's Kitchen Private Mezzanine - Apartments for Rent in New York, New York, United States
address:  <a class="_5twioja" href="https://airbnb.com/s/New%20York/homes" rel="noopener noreferrer" target="_blank">New York, United States</a>
airbnb_name_tag:  <h1 class="_14i3z6h" tabindex="-1">Heart of Hell's Kitchen Private Mezzanine</h1>
price_tag:  <span aria-hidden="true" class="_pgfqnw">$68</span>
num_reviews_tag:  <span class="_goo6eo"><span class="_krjbj">4.69 out of 5 stars from 138 reviews</span><div dir="ltr">4.69 (138 reviews)</div></span>
secondary_ratings:  [<span aria-hidden="true" class="_4oybiu">4.8</span>, <span aria-hidden="true" class="_4oybiu">4.8</span>, <span aria-hidden="true" class="_4oybiu">4.9</span>, <span aria-hidden="true" class="_4oybiu">4.9</span>, <span aria-hidden="true" class="_4oybiu">4.9</span>, <span aria-hidden="true" class="_4oybiu">4.7</span>]
amenities_tag:  [<div class="_1nlbjeu"><div>Kitchen</div><div class="_yp1t7a"><svg aria-hidd

...

Title:  Home away from home - Apartments for Rent in Brooklyn, New York, United States
address:  <a class="_5twioja" href="https://airbnb.com/s/Brooklyn/homes" rel="noopener noreferrer" target="_blank">Brooklyn, New York, United States</a>
airbnb_name_tag:  <h1 class="_14i3z6h" tabindex="-1">Home away from home</h1>
price_tag:  <span aria-hidden="true" class="_pgfqnw">$65</span>
num_reviews_tag:  <span class="_goo6eo"><span class="_krjbj">5.0 out of 5 stars from 6 reviews</span><div dir="ltr">5.0 (6 reviews)</div></span>
secondary_ratings:  [<span aria-hidden="true" class="_4oybiu">4.8</span>, <span aria-hidden="true" class="_4oybiu">5.0</span>, <span aria-hidden="true" class="_4oybiu">5.0</span>, <span aria-hidden="true" class="_4oybiu">5.0</span>, <span aria-hidden="true" class="_4oybiu">5.0</span>, <span aria-hidden="true" class="_4oybiu">5.0</span>]
amenities_tag:  [<div class="_1nlbjeu"><div>Kitchen</div><div class="_yp1t7a"><svg aria-hidden="true" role="presentation" style="displ

Title:  Artistic NEW LOFT 4 br/2 bath in Times Sq - Lofts for Rent in New York, New York, United States
address:  <a class="_5twioja" href="https://airbnb.com/s/New%20York/homes" rel="noopener noreferrer" target="_blank">New York, United States</a>
airbnb_name_tag:  <h1 class="_14i3z6h" tabindex="-1">Artistic NEW LOFT 4 br/2 bath in Times Sq</h1>
price_tag:  <span aria-hidden="true" class="_pgfqnw">$387</span>
num_reviews_tag:  <span class="_goo6eo"><span class="_krjbj">4.59 out of 5 stars from 92 reviews</span><div dir="ltr">4.59 (92 reviews)</div></span>
secondary_ratings:  [<span aria-hidden="true" class="_4oybiu">4.7</span>, <span aria-hidden="true" class="_4oybiu">4.6</span>, <span aria-hidden="true" class="_4oybiu">4.7</span>, <span aria-hidden="true" class="_4oybiu">4.8</span>, <span aria-hidden="true" class="_4oybiu">4.6</span>, <span aria-hidden="true" class="_4oybiu">4.5</span>]
amenities_tag:  [<div class="_1nlbjeu"><div>Kitchen</div><div class="_yp1t7a"><svg aria-hidden="tr

Title:  Private 4 BR apartment 25 mins from NYC!! - Apartments for Rent in Bayonne, New Jersey, United States
address:  <a class="_5twioja" href="https://airbnb.com/s/Bayonne/homes" rel="noopener noreferrer" target="_blank">Bayonne, New Jersey, United States</a>
airbnb_name_tag:  <h1 class="_14i3z6h" tabindex="-1">Private 4 BR apartment 25 mins from NYC!!</h1>
price_tag:  <span aria-hidden="true" class="_pgfqnw">$130</span>
num_reviews_tag:  <span class="_goo6eo"><span class="_krjbj">4.83 out of 5 stars from 18 reviews</span><div dir="ltr">4.83 (18 reviews)</div></span>
secondary_ratings:  [<span aria-hidden="true" class="_4oybiu">4.5</span>, <span aria-hidden="true" class="_4oybiu">5.0</span>, <span aria-hidden="true" class="_4oybiu">5.0</span>, <span aria-hidden="true" class="_4oybiu">4.7</span>, <span aria-hidden="true" class="_4oybiu">5.0</span>, <span aria-hidden="true" class="_4oybiu">4.7</span>]
amenities_tag:  [<div class="_1nlbjeu"><div>Kitchen</div><div class="_yp1t7a"><svg a

Title:  City Queen – Terrace ADA - Boutique hotels for Rent in New York, New York, United States
address:  <a class="_5twioja" href="https://airbnb.com/s/New%20York/homes" rel="noopener noreferrer" target="_blank">New York, United States</a>
airbnb_name_tag:  <h1 class="_14i3z6h" tabindex="-1">City Queen – Terrace ADA</h1>
price_tag:  <span aria-hidden="true" class="_pgfqnw">$79</span>
num_reviews_tag:  None
secondary_ratings:  []
amenities_tag:  [<div class="_1nlbjeu"><div>Elevator</div><div class="_yp1t7a"><svg aria-hidden="true" role="presentation" style="display: block; height: 24px; width: 24px; fill: currentcolor;" viewbox="0 0 32 32" xmlns="http://www.w3.org/2000/svg"><path d="M30 1a1 1 0 0 1 .993.883L31 2v28a1 1 0 0 1-.883.993L30 31H2a1 1 0 0 1-.993-.883L1 30V2a1 1 0 0 1 .883-.993L2 1zM3 3v26h12V3zm7 9v6.585l1.793-1.792 1.414 1.414-3.5 3.5a1 1 0 0 1-1.32.083l-.094-.083-3.5-3.5 1.414-1.414L8 18.585V12zm12.387-1.497a1 1 0 0 1 1.226 0l.094.083 3.5 3.5-1.414 1.414L24 13.707V20h-2v-

IndexError: list index out of range

In [134]:
df 

Airbnb_Name Price Primary_Rating  \
0                                            City King    79           4.93   
1    A room in private house - 20-35 minutes  from NYC    24           4.66   
2             Cozy, comfort close to LaGuardia Airport    30           4.94   
3                       Private room in Queens, Ny # 1    26           4.89   
4                          Greatest Deal near EWR/NYC!    27           4.70   
5            Heart of Hell's Kitchen Private Mezzanine    68           4.69   
6         Super Stylish & Spacious Manhattan Apartment   111           4.86   
7    Kosy apt w modern new furniture in the heart o...   123           4.32   
8                                 HenzStay in Brooklyn   100           4.90   
9                 Brand New Apartment Earshot from NYC    65           4.83   
10                The Hotel @ New York City, Queen Bed    87           4.14   
11                                 Home away from home    65            5.0   
12           Sunny Studio Apartment on Upper East Side   150           4.83   
13                  Williamsburg private clean cozy RM    60           4.73   
14   Beautifully modern Madison Avenue luxury building   118              0   
15                       Jersey City Heights Apartment   102           4.89   
16                 Private Room Walking to Time Square    85           4.26   
17           Artistic NEW LOFT 4 br/2 bath in Times Sq   387           4.59   
18           Private 4 BR apartment 25 mins from NYC!!   130           4.83   
19                            City Queen – Terrace ADA    79              0   
20       The Best Place In Brklyn - Close To Manhattan    50           4.33   
21                          Beautiful Sunny Small Room    50           4.65   
22       Stunning 3 Bedroom Home minutes away from NYC    99           4.53   
23     Daily sanitized Entire Private Suite near NYC!!    55           4.69   
24    Modern, spacious, private 3 BR home close to NYC   161           4.97   
25                  Williamsburg private clean cozy RM    60           4.73   
26                 Private Room Walking to Time Square    85           4.26   
27                 Big apartment, comfy - calm bedroom    72           4.86   
28      Large 1 Bedroom Three Blocks from Central Park    65           4.74   
29        A neat bedroom in a cozy 3-bedroom apartment    75           4.96   
..                                                 ...   ...            ...   
712     Large 1 Bedroom Three Blocks from Central Park    65           4.74   
713       A neat bedroom in a cozy 3-bedroom apartment    75           4.96   
714          Charming and Trendy Brownstone near Train   885           4.91   
715  Modern Apt. 15 min to Manhattan/NYC-Free Parking-   105           4.51   
716                     Room for one at Stella's place    25           4.99   
717   new sunshine room in chinatown train F is around    82           4.77   
718        Large Private Suite in the Heart of Midtown   191           3.85   
719                                         City Queen    91           4.77   
720               Midtown Manhattan - Cozy Triple Room   159           4.75   
721  See the Battery in 5 Star Luxury with the Family.   177            5.0   
722                                          City King    79           4.93   
723           Cozy, comfort close to LaGuardia Airport    30           4.94   
724  A room in private house - 20-35 minutes  from NYC    24           4.66   
725                     Private room in Queens, Ny # 1    26           4.89   
726  Kosy apt w modern new furniture in the heart o...   123           4.32   
727          Heart of Hell's Kitchen Private Mezzanine    68           4.69   
728                        Greatest Deal near EWR/NYC!    27           4.70   
729                               HenzStay in Brooklyn   100           4.90   
730               Brand New Apartment Earshot from NYC    65           4.83   
731       Supe

In [135]:
dump(df, 'airbnb_dataframe.pkl', compress=True)
df.to_csv('airbnb_hotels.csv')